## df1 : 1.부산시남구_주정차위반이력.csv
주정차위반이력의 좌표와 격자, 동을 찾는 파일

## 라이브러리, 데이터프레임

In [1]:
!pip3 install shapely
#!pip3 install --upgrade setuptools

from geoband.API import *
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import pandas as pd
import folium
import numpy as np
import googlemaps
import math
import matplotlib as mpl
from IPython.core.display import display, HTML
from shapely.geometry import Point, Polygon
pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 100)
pd.set_option('max_rows', 300)
plt.rc('font', family='NanumGothic')
mpl.rc('axes', unicode_minus=False)

GetCompasData('SBJ_2107_003', '1', '1.부산시남구_주정차위반이력.csv')
GetCompasData('SBJ_2107_003', '14', '14.부산시남구_행정경계(읍면동).geojson')
GetCompasData('SBJ_2107_003', '15', '15.부산시남구_격자(300X300).geojson')

df1 = pd.read_csv('./1.부산시남구_주정차위반이력.csv')
df14 = json.load(open('./14.부산시남구_행정경계(읍면동).geojson'))
df15 = json.load(open('./15.부산시남구_격자(300X300).geojson'))
df18 = gpd.read_file('./14.부산시남구_행정경계(읍면동).geojson')
df19 = gpd.read_file('./15.부산시남구_격자(300X300).geojson')

/opt/app-root/lib/python3.6/site-packages/geopandas/_compat.py:110: UserWarning: The Shapely GEOS version (3.8.0-CAPI-1.13.1 ) is incompatible with the GEOS version PyGEOS was compiled with (3.9.0-CAPI-1.16.2). Conversions between both will be slow.
  shapely_geos_version, geos_capi_version_string


In [2]:
df1

cd_date                   cd_loc              cd_cm_addr    cd_type
0       2018-09-17      용호동 분포로 하이츠자이 상가 부근         강원도 강릉시 강동면 단경로     스마트폰단속
1       2018-10-31            용호동 현대비치앞CCTV            강원도 강릉시 강릉대로  고정형CCTV단속
2       2018-12-10     대연동 대천사거리CCTV(자전거도로)            강원도 강릉시 강릉대로  고정형CCTV단속
3       2018-03-11            대연동 대연사거리CCTV             강원도 강릉시 강변로  고정형CCTV단속
4       2018-01-22          대연동 수영로 대연성당 부근             강원도 강릉시 범일로     스마트폰단속
...            ...                      ...                     ...        ...
152677  2021-03-31           대연동 남구청사거리CCTV        경상남도 양산시 동면 석산1길  고정형CCTV단속
152678  2021-03-31          대연동 교보문고 앞 CCTV      충청남도 당진시 합덕읍 미락2안길  고정형CCTV단속
152679  2021-03-31           대연동 대천초삼거리CCTV           울산광역시 중구 도화골길  고정형CCTV단속
152680  2021-03-31           대연동 클럽클리오앞CCTV           부산광역시 영도구 하나길  고정형CCTV단속
152681  2021-03-31  감만동 양지골로 342 부근(교차로모퉁이)  경상남도 창원시 마산합포구 구산면 양평길       민원신고

[152682 rows x 4 columns]

## df1에서 한 건의 주정차위반이 발생한 cd_loc 7000건을 삭제
152682건의 주정차위반 중 한 건의 주정차위반이 발생한 지역을 제외하고 <br>
144882건의 주정차위반 좌표를 검색 <br>

In [3]:
temp = df1.groupby('cd_loc').size().sort_values(ascending=False)[8000:].keys()
df1 = df1[[not i for i in df1['cd_loc'].isin(temp)]]
df1

cd_date                   cd_loc              cd_cm_addr    cd_type
0       2018-09-17      용호동 분포로 하이츠자이 상가 부근         강원도 강릉시 강동면 단경로     스마트폰단속
1       2018-10-31            용호동 현대비치앞CCTV            강원도 강릉시 강릉대로  고정형CCTV단속
2       2018-12-10     대연동 대천사거리CCTV(자전거도로)            강원도 강릉시 강릉대로  고정형CCTV단속
3       2018-03-11            대연동 대연사거리CCTV             강원도 강릉시 강변로  고정형CCTV단속
4       2018-01-22          대연동 수영로 대연성당 부근             강원도 강릉시 범일로     스마트폰단속
...            ...                      ...                     ...        ...
152677  2021-03-31           대연동 남구청사거리CCTV        경상남도 양산시 동면 석산1길  고정형CCTV단속
152678  2021-03-31          대연동 교보문고 앞 CCTV      충청남도 당진시 합덕읍 미락2안길  고정형CCTV단속
152679  2021-03-31           대연동 대천초삼거리CCTV           울산광역시 중구 도화골길  고정형CCTV단속
152680  2021-03-31           대연동 클럽클리오앞CCTV           부산광역시 영도구 하나길  고정형CCTV단속
152681  2021-03-31  감만동 양지골로 342 부근(교차로모퉁이)  경상남도 창원시 마산합포구 구산면 양평길       민원신고

[144882 rows x 4 columns]

## latlong : 2건 이상의 주정차위반이 발생한 cd_loc 8000개의 좌표를 찾는 지오코딩

In [4]:
# gmaps = googlemaps.Client(key='')

# df1_1 = pd.DataFrame({'cd_loc' : df1['cd_loc'].unique()})

# temp_loc = df1_1['cd_loc']
# temp_latlong = {}

# for loc in temp_loc:
#   geocode_result = gmaps.geocode((loc), language='ko')
#   if len(geocode_result) > 0 :
#     temp_latlong[loc] = [geocode_result[0]['geometry']['location']['lat'], geocode_result[0]['geometry']['location']['lng']]

# for i in range(len(df1_1)):
#   df1_1.loc[i, 'latlong'] = temp_latlong[df1_1['cd_loc'].loc[i]]
    
# df1_1.to_csv('latlong.csv')

In [5]:
latlong = pd.read_csv('./latlong.csv').drop('Unnamed: 0', axis=1)
latlong

cd_loc                           latlong
0        용호동 분포로 하이츠자이 상가 부근         [35.1327668, 129.1109547]
1              용호동 현대비치앞CCTV  [35.12595260000001, 129.1098341]
2       대연동 대천사거리CCTV(자전거도로)         [35.1083946, 128.9308709]
3              대연동 대연사거리CCTV          [35.134505, 129.0934742]
4            대연동 수영로 대연성당 부근         [35.1347825, 129.0985851]
...                      ...                               ...
7966      대연동 유엔로157번가길 3 부근         [35.1321438, 129.0935301]
7967  대연동 못골로 96 부근(교차로 모퉁이)         [35.1355868, 129.0927585]
7968       용호동 신선대산복로 203 부근         [35.1119505, 129.1034747]
7969      대연동 수영로334번길 56 부근         [35.1361482, 129.1036105]
7970     대연동 못골번영로71번길 12 부근         [35.1422536, 129.0845862]

[7971 rows x 2 columns]

## 지오코딩으로 검색되지 않은 좌표(missing) 처리

In [6]:
temp = df1[[not i for i in df1['cd_loc'].isin(latlong['cd_loc'])]]
temp['cd_loc'].unique()

array(['용호동 SK뷰@앞 인도CCTV(곡각/횡단보도)', '용호1 행정복지센터CCTV',
       '용호동 솔밭공원부근CCTV(곡각/횡단보도)', '용호4동 하나로마트 부근',
       '대연동 진남로127번길 한누리 어린이집\n구화학교 부근', '문현동 진남로 인각사 부근(인도)',
       '용호동 솔밭공원부근CCTV(곡각/횡단보도 위)', '대연4동 산업인력공단 부근(인도)', '용호4동 하나로마트부근',
       '대연4동 효한의원부근', '감만 천지매매상사앞CCTV(1차선주차)', '용호3동 새마을금고부근',
       '용호3동 새마을금고 부근', '용호1동 삼신스타빌라부근(횡단보도)', '용호1동 삼신스타빌라부근',
       '용호3동 동아맨션부근', '문현1동 자유평화로60번길 부근', '용호동 솔밭공원부근CCTV(곡각/횡단보도위)',
       '대연4동 효한의원 부근', '우암2동 장고개로부근', '대연4동 성림빌라부근', '우암1동 대성하이아트부근',
       '우암1동 중앙하이츠부근', '대연1동 키즈클럽 부근', '문현동 진남로 인각사 부근(횡단보도)',
       '문현동 진남로 인각사 부근(도로가운데주차)', '용당동 신선로 309-1 부근(인도)',
       '대연6동 부산성소병원 부근(인도)', '대연동 수영로266번길 46 부근(곡각지)',
       '우암1동 디도비홈시스템부근(인도)'], dtype=object)

In [7]:
missing = {}
missing['용호동 SK뷰@앞 인도CCTV(곡각/횡단보도)'] = [35.101506, 129.116664]
missing['용호1 행정복지센터CCTV'] = [35.12113661533387, 129.11261489787017]
missing['용호동 솔밭공원부근CCTV(곡각/횡단보도)'] = [35.12011226872462, 129.10855254019688]
missing['용호4동 하나로마트 부근'] = [35.11208971641365, 129.11080815554305]
missing['대연동 진남로127번길 한누리 어린이집\n구화학교 부근'] = [35.13747022944396, 129.07793968066778]
missing['문현동 진남로 인각사 부근(인도)'] = [35.146983835156185, 129.07518288252442]
missing['용호동 솔밭공원부근CCTV(곡각/횡단보도 위)'] = [35.1200859418365, 129.1085739978701]
missing['대연4동 산업인력공단 부근(인도)'] = [35.12658859572853, 129.10142589589725]
missing['용호4동 하나로마트부근'] = [35.11200195144535, 129.1107866978698]
missing['대연4동 효한의원부근'] = [35.12803583265557, 129.08933384879856]
missing['감만 천지매매상사앞CCTV(1차선주차)'] = [35.111542105789745, 129.08235485073897]
missing['용호3동 새마을금고부근'] = [35.12171677617277, 129.11186822455633]
missing['용호3동 새마을금고 부근'] = [35.12171677617277, 129.11186822455633]
missing['용호1동 삼신스타빌라부근(횡단보도)'] = [35.12116457601293, 129.10864154765463]
missing['용호1동 삼신스타빌라부근'] = [35.12116457601293, 129.10864154765463]
missing['용호3동 동아맨션부근'] = [35.12069942902944, 129.11239469085058]
missing['문현1동 자유평화로60번길 부근'] = [35.13966261852536, 129.06666313041964]
missing['용호동 솔밭공원부근CCTV(곡각/횡단보도위)'] = [35.1200947174668, 129.10849889601377]
missing['대연4동 효한의원 부근'] = [35.12803583265557, 129.08933384879856]
missing['우암2동 장고개로부근'] = [35.13101098828017, 129.07055429892753]
missing['대연4동 성림빌라부근'] = [35.132955576065584, 129.0901924482709]
missing['우암1동 대성하이아트부근'] = [35.127781626193034, 129.0835159825237]
missing['우암1동 중앙하이츠부근'] = [35.12733752724585, 129.08226518252386]
missing['대연1동 키즈클럽 부근'] = [35.13075814865869, 129.0974716671774]
missing['문현동 진남로 인각사 부근(횡단보도)'] = [35.146690, 129.075028]
missing['문현동 진남로 인각사 부근(도로가운데주차)'] = [35.146690, 129.075028]
missing['용당동 신선로 309-1 부근(인도)'] = [35.1138181737015, 129.0954650534225]
missing['대연6동 부산성소병원 부근(인도)'] = [35.13521955660275, 129.0856806248508]
missing['대연동 수영로266번길 46 부근(곡각지)'] = [35.134744961541536, 129.09756068252398]
missing['우암1동 디도비홈시스템부근(인도)'] = [35.12220589025863, 129.08107349787014]

missing_key, missing_value = list(missing.keys()), list(missing.values())

for i in range(len(missing_key)):
    latlong.loc[7971+i] = [missing_key[i], str(missing_value[i])]
    
latlong['lat'] = latlong.latlong.str.split(',').str[0].str.strip('[').astype(float)
latlong['long'] = latlong.latlong.str.split(',').str[1].str.strip(']').astype(float)
latlong

cd_loc                                   latlong  \
0         용호동 분포로 하이츠자이 상가 부근                 [35.1327668, 129.1109547]   
1               용호동 현대비치앞CCTV          [35.12595260000001, 129.1098341]   
2        대연동 대천사거리CCTV(자전거도로)                 [35.1083946, 128.9308709]   
3               대연동 대연사거리CCTV                  [35.134505, 129.0934742]   
4             대연동 수영로 대연성당 부근                 [35.1347825, 129.0985851]   
...                       ...                                       ...   
7996  문현동 진남로 인각사 부근(도로가운데주차)                    [35.14669, 129.075028]   
7997     용당동 신선로 309-1 부근(인도)     [35.1138181737015, 129.0954650534225]   
7998       대연6동 부산성소병원 부근(인도)    [35.13521955660275, 129.0856806248508]   
7999  대연동 수영로266번길 46 부근(곡각지)  [35.134744961541536, 129.09756068252398]   
8000       우암1동 디도비홈시스템부근(인도)   [35.12220589025863, 129.08107349787014]   

            lat        long  
0     35.132767  129.110955  
1     35.125953  129.109834  
2     35.108395  128.930871  
3     35.134505  129.093474  
4     35.134783  129.098585  
...         ...         ...  
7996  35.146690  129.075028  
7997  35.113818  129.095465  
7998  35.135220  129.085681  
7999  35.134745  129.097561  
8000  35.122206  129.081073  

[8001 rows x 4 columns]

## 지오코딩으로 찾은 좌표(latlong)와 남구 격자(df15)를 매핑
주정차위반의 좌표와 격자를 찾는 코드 <br>
null 값은 남구 밖이라서 제외

In [8]:
m = folium.Map(location=[35.126703, 129.100194], zoom_start=13, prefer_canvas=True)

folium.GeoJson(df15).add_to(m)

for i in range(len(latlong)):
    if i % 10 == 0:
        folium.Circle(location = [latlong['lat'].iloc[i], latlong['long'].iloc[i]], 
                      radius=1, color='green', fill_color='green', fill_opacity=0.3, 
                      line_opcity=0.1, tooltip = latlong['cd_loc'].iloc[i]).add_to(m)
m

In [9]:
# for i in range(len(latlong)):
#     for j in range(len(df15['features'])):
#         if Point(latlong[['long', 'lat']].iloc[i]).within(Polygon(df15['features'][j]['geometry']['coordinates'][0])) == True:
#             print(df15['features'][j]['properties']['id'])
#             latlong.loc[i, 'district'] = df15['features'][j]['properties']['id']
#     if i % 1 == 0:
#             print(i)
# latlong.to_csv('latlongid.csv')

In [10]:
df17 = pd.read_csv('./latlongid.csv')
df17 = df17.dropna(axis=0)
df17 = df17.drop(['Unnamed: 0.1', 'latlong'], axis=1)
df17['district'] = df17['district'].astype(int)
df17.rename(columns = {'district' : 'id'}, inplace = True)
df17

cd_loc        lat        long   id
0         용호동 분포로 하이츠자이 상가 부근  35.132767  129.110955  608
1               용호동 현대비치앞CCTV  35.125953  129.109834  612
3               대연동 대연사거리CCTV  35.134505  129.093474  398
4             대연동 수영로 대연성당 부근  35.134783  129.098585  468
5           용호동 이기대공원로 동생말 부근  35.131845  129.121145  749
...                       ...        ...         ...  ...
7996  문현동 진남로 인각사 부근(도로가운데주차)  35.146690  129.075028  147
7997     용당동 신선로 309-1 부근(인도)  35.113818  129.095465  442
7998       대연6동 부산성소병원 부근(인도)  35.135220  129.085681  292
7999  대연동 수영로266번길 46 부근(곡각지)  35.134745  129.097561  433
8000       우암1동 디도비홈시스템부근(인도)  35.122206  129.081073  228

[7900 rows x 4 columns]

## id(격자)가 어떤 동에 속하는지 찾아서 매핑
cd_loc을 슬라이싱하여 쓰지 않는 이유는 정확히 몇동인지 알 수 없기 때문

In [11]:
m = folium.Map(location=[35.126703, 129.100194], zoom_start=13, prefer_canvas=True)

folium.GeoJson(df15).add_to(m)
folium.GeoJson(df14).add_to(m)

m

In [12]:
temp = df17['id'].unique()
dong = {}
for i in temp:
    for j in range(len(df18)):
        if (df19[df19['id'] == i]['geometry'].centroid).within(df18['geometry'].iloc[j]).bool() == True:
            dong[i] = df18['ADM_DR_NM'].iloc[j]

dong

/opt/app-root/lib/python3.6/site-packages/ipykernel_launcher.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  """
/opt/app-root/lib/python3.6/site-packages/ipykernel_launcher.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  """
/opt/app-root/lib/python3.6/site-packages/ipykernel_launcher.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  """
/opt/app-root/lib/python3.6/site-packages/ipykernel_launcher.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CR

{608: '용호1동',
 612: '용호1동',
 398: '대연1동',
 468: '대연3동',
 749: '용호3동',
 83: '문현4동',
 727: '용호2동',
 501: '대연3동',
 184: '문현1동',
 113: '문현1동',
 364: '대연1동',
 298: '감만2동',
 44: '문현2동',
 327: '대연5동',
 649: '용호3동',
 268: '감만1동',
 366: '대연4동',
 618: '용호4동',
 502: '대연3동',
 432: '대연5동',
 644: '용호1동',
 46: '문현2동',
 231: '감만1동',
 292: '대연6동',
 257: '대연6동',
 42: '문현2동',
 622: '용호4동',
 226: '우암동',
 362: '대연5동',
 536: '대연3동',
 679: '용호1동',
 81: '문현3동',
 80: '문현3동',
 330: '대연4동',
 332: '대연4동',
 331: '대연4동',
 614: '용호1동',
 500: '대연3동',
 365: '대연4동',
 183: '문현1동',
 465: '대연3동',
 86: '우암동',
 363: '대연1동',
 680: '용호1동',
 686: '용호3동',
 8: '문현2동',
 503: '대연3동',
 149: '문현3동',
 252: '문현1동',
 121: '우암동',
 115: '문현3동',
 326: '대연5동',
 264: '감만2동',
 427: '대연3동',
 9: '문현2동',
 230: '감만1동',
 399: '대연1동',
 434: '대연1동',
 234: '감만1동',
 520: '용호4동',
 293: '대연1동',
 429: '대연3동',
 291: '대연6동',
 116: '문현3동',
 157: '우암동',
 267: '감만1동',
 148: '문현1동',
 333: '대연4동',
 43: '문현2동',
 195: '감만1동',
 233: '감만1동',
 652: '용호2동',
 395: '대

## 경계에 위치한 점의 동을 찾는 코드

In [13]:
missing = []
for i in temp:
    if i in dong.keys():
        pass
    else :
        missing.append(i)
missing

[10, 125, 571, 126, 6, 657, 714, 606, 678, 41, 421]

In [14]:
m = folium.Map(location=[35.126703, 129.100194], zoom_start=13, prefer_canvas=True)

folium.GeoJson(df14).add_to(m)

for i in missing:

    folium.Circle(location = [df17[df17['id'] == i]['lat'].iloc[0], df17[df17['id'] == i]['long'].iloc[0]], radius=100, color='red', fill_color='red', fill_opacity=0.1, line_opcity=0.1, tooltip = df17[df17['id'] == i]['id'].iloc[0]).add_to(m)

m

In [15]:
dong[6] = '문현2동'
dong[41] = '문현2동'
dong[10] = '문현2동'
dong[125] = '감만1동'
dong[126] = '감만1동'
dong[421] = '대연3동'
dong[571] = '대연3동'
dong[606] = '대연3동'
dong[678] = '용호1동'
dong[714] = '용호3동'
dong[657] = '용호2동'

In [16]:
temp = pd.DataFrame({'id' : dong.keys(), 'dong' : dong.values()})
df17 = pd.merge(df17, temp, how='inner', on='id')
df17

cd_loc        lat        long   id  dong
0           용호동 분포로 하이츠자이 상가 부근  35.132767  129.110955  608  용호1동
1       용호동 신선로 566 부근(교차로 모퉁이)  35.132767  129.110955  608  용호1동
2             용호1동 GS하이츠자이아파트부근  35.132755  129.110947  608  용호1동
3          용호동 분포로 하이츠자이 아파트 부근  35.132755  129.110947  608  용호1동
4           용호동 신선로 566 부근(정류장)  35.132767  129.110955  608  용호1동
...                         ...        ...         ...  ...   ...
7895       용호동 분포로 41 부근(횡단보도위)  35.128879  129.114015  645  용호1동
7896             대연동 황령산구름고개 부근  35.159354  129.095850  421  대연3동
7897                대연동 황령산구름고개  35.159354  129.095850  421  대연3동
7898            대연동 황령산 구름고개 부근  35.159354  129.095850  421  대연3동
7899  용호동 SK뷰@앞 인도CCTV(곡각/횡단보도)  35.101506  129.116664  693  용호2동

[7900 rows x 5 columns]

## df1(주정차위반)에 좌표와 격자, 동 추가

In [17]:
df1

cd_date                   cd_loc              cd_cm_addr    cd_type
0       2018-09-17      용호동 분포로 하이츠자이 상가 부근         강원도 강릉시 강동면 단경로     스마트폰단속
1       2018-10-31            용호동 현대비치앞CCTV            강원도 강릉시 강릉대로  고정형CCTV단속
2       2018-12-10     대연동 대천사거리CCTV(자전거도로)            강원도 강릉시 강릉대로  고정형CCTV단속
3       2018-03-11            대연동 대연사거리CCTV             강원도 강릉시 강변로  고정형CCTV단속
4       2018-01-22          대연동 수영로 대연성당 부근             강원도 강릉시 범일로     스마트폰단속
...            ...                      ...                     ...        ...
152677  2021-03-31           대연동 남구청사거리CCTV        경상남도 양산시 동면 석산1길  고정형CCTV단속
152678  2021-03-31          대연동 교보문고 앞 CCTV      충청남도 당진시 합덕읍 미락2안길  고정형CCTV단속
152679  2021-03-31           대연동 대천초삼거리CCTV           울산광역시 중구 도화골길  고정형CCTV단속
152680  2021-03-31           대연동 클럽클리오앞CCTV           부산광역시 영도구 하나길  고정형CCTV단속
152681  2021-03-31  감만동 양지골로 342 부근(교차로모퉁이)  경상남도 창원시 마산합포구 구산면 양평길       민원신고

[144882 rows x 4 columns]

In [18]:
df1 = pd.merge(df1, df17, how='inner', on='cd_loc')
df1

cd_date               cd_loc            cd_cm_addr cd_type  \
0       2018-09-17  용호동 분포로 하이츠자이 상가 부근       강원도 강릉시 강동면 단경로  스마트폰단속   
1       2018-01-11  용호동 분포로 하이츠자이 상가 부근      경기도 성남시 중원구 갈마치로  스마트폰단속   
2       2018-01-11  용호동 분포로 하이츠자이 상가 부근       경기도 성남시 중원구 금상로  스마트폰단속   
3       2018-02-08  용호동 분포로 하이츠자이 상가 부근       경기도 양주시 은현면 화합로  스마트폰단속   
4       2019-02-01  용호동 분포로 하이츠자이 상가 부근          경상남도 김해시 유하로  스마트폰단속   
...            ...                  ...                   ...     ...   
139314  2020-04-20    용호동 신선대산복로 203 부근    울산광역시 울주군 범서읍 굴화1길  스마트폰단속   
139315  2020-06-14    용호동 신선대산복로 203 부근    울산광역시 울주군 범서읍 굴화1길  스마트폰단속   
139316  2020-09-16   대연동 수영로334번길 56 부근    경상북도 경주시 외동읍 모화남1길  스마트폰단속   
139317  2020-09-22  대연동 못골번영로71번길 12 부근  경상남도 창원시 마산합포구 노산남4길  스마트폰단속   
139318  2020-09-22  대연동 못골번영로71번길 12 부근  경상남도 창원시 마산합포구 성호서5길  스마트폰단속   

              lat        long   id  dong  
0       35.132767  129.110955  608  용호1동  
1       35.132767  129.110955  608  용호1동  
2       35.132767  129.110955  608  용호1동  
3       35.132767  129.110955  608  용호1동  
4       35.132767  129.110955  608  용호1동  
...           ...         ...  ...   ...  
139314  35.111950  129.103475  548   용당동  
139315  35.111950  129.103475  548   용당동  
139316  35.136148  129.103611  537  대연3동  
139317  35.142254  129.084586  289  대연5동  
139318  35.142254  129.084586  289  대연5동  

[139319 rows x 8 columns]

In [19]:
df1.to_csv('df.csv', index=False)